# Fixed


## Working examples


### global annotation (example from tests)


In [ ]:
from dewret.renderers.cwl import render
from dewret.tasks import task, construct, workflow
from dewret.annotations import Fixed

list_2: Fixed[list[int]] = [0, 1, 2, 3]

@workflow()
def loop_over_lists(list_1: list[int]) -> list[int]:
    result = []
    for a, b in zip(list_1, list_2, strict=False):
        result.append(a + b + len(list_2))
    return result


result = loop_over_lists(list_1=[10, 20, 30, 40])
workflow = construct(result, simplify_ids=True)
cwl = render(workflow)
cwl

{'__root__': {'cwlVersion': 1.2,
  'class': 'Workflow',
  'inputs': {'loop_over_lists-1-list_1': {'label': 'list_1',
    'type': 'array',
    'items': 'int',
    'default': [10, 20, 30, 40]}},
  'outputs': {'out': {'label': 'out',
    'type': 'array',
    'items': 'int',
    'outputSource': 'loop_over_lists-1/out'}},
  'steps': {'loop_over_lists-1': {'run': 'loop_over_lists',
    'in': {'list_1': {'source': 'loop_over_lists-1-list_1'}},
    'out': ['out']}}},
 'loop_over_lists-1': {'cwlVersion': 1.2,
  'class': 'Workflow',
  'inputs': {},
  'outputs': {'out': {'type': 'float',
    'label': 'out',
    'expression': '[list_1[0] + list_2[0] + 4, list_1[1] + list_2[1] + 4, list_1[2] + list_2[2] + 4, list_1[3] + list_2[3] + 4]',
    'source': ['list_1', 'list_2']}},
  'steps': {}}}

### parameter annotation


In [1]:
from dewret.renderers.cwl import render
from dewret.tasks import construct, workflow
from dewret.annotations import Fixed

@workflow()
def loop_over_lists(list_1: Fixed[list[int]]) -> list[int]:
    result = []
    for a, b in zip(list_1, list_1, strict=False):
        result.append(a + b + len(list_1))
    return result


result = loop_over_lists(list_1=[10, 20, 30, 40])
workflow = construct(result, simplify_ids=True)
cwl = render(workflow)
cwl

{'__root__': {'cwlVersion': 1.2,
  'class': 'Workflow',
  'inputs': {'loop_over_lists-1-list_1': {'label': 'list_1',
    'type': 'array',
    'items': 'int',
    'default': [10, 20, 30, 40]}},
  'outputs': {'out': {'label': 'out',
    'type': 'array',
    'items': 'int',
    'outputSource': 'loop_over_lists-1/out'}},
  'steps': {'loop_over_lists-1': {'run': 'loop_over_lists',
    'in': {'list_1': {'source': 'loop_over_lists-1-list_1'}},
    'out': ['out']}}},
 'loop_over_lists-1': {'cwlVersion': 1.2,
  'class': 'Workflow',
  'inputs': {},
  'outputs': {'out': {'type': 'float',
    'label': 'out',
    'expression': '[2*list_1[0] + 4, 2*list_1[1] + 4, 2*list_1[2] + 4, 2*list_1[3] + 4]',
    'source': ['list_1']}},
  'steps': {}}}

### simple iteration of a task over a list


This example shows the main use of the Fixed annotation


In [ ]:
""" from dewret.renderers.cwl import render
from dewret.tasks import construct, workflow, task
from dewret.annotations import Fixed

@task()
def work(arg: int) -> int:
    # do work
    return arg # need to return something or the loop is optimized away

@workflow()
def loop_work(list: Fixed[list[int]]) -> list[int]:
    # result = []
    # for i in list:
    #     work(arg = i)
    #     result.append(i) 
    result = [work(arg = i) for i in list]

    return result

result = loop_work(list=[1,2])
workflow = construct(result, simplify_ids=True)
cwl = render(workflow)
cwl """

TaskException: name 'work' is not defined

In [16]:
cwl.keys()

dict_keys(['__root__', 'loop_work-1'])

In [18]:
cwl['loop_work-1']['steps']

{'work-1-1': {'run': 'work',
  'in': {'arg': {'source': 'list[1]'}},
  'out': ['out']},
 'work-1-2': {'run': 'work',
  'in': {'arg': {'source': 'list[0]'}},
  'out': ['out']}}

### Render time loops don't have to be annotated as `Fixed`


In [ ]:
from dewret.renderers.cwl import render
from dewret.tasks import construct, workflow, task
from dewret.annotations import AtRender

list_2: AtRender[list[int]] = [0, 1, 2, 3]

# This task is needed to ensure something gets rendered, note the type isn't enforced
@task()
def iden(arg: str) -> str:
    return arg

@workflow()
def loop_over_lists() -> list[int]:
    result = []
    for a, b in zip(list_2, list_2, strict=False):
        result.append(a + b + len(list_2))
    return iden(arg = result)

result = loop_over_lists()
workflow = construct(result, simplify_ids=True)
cwl = render(workflow)
cwl

{'__root__': {'cwlVersion': 1.2,
  'class': 'Workflow',
  'inputs': {},
  'outputs': {'out': {'label': 'out',
    'type': 'array',
    'items': 'int',
    'outputSource': 'loop_over_lists-1/out'}},
  'steps': {'loop_over_lists-1': {'run': 'loop_over_lists',
    'in': {},
    'out': ['out']}}},
 'loop_over_lists-1': {'cwlVersion': 1.2,
  'class': 'Workflow',
  'inputs': {},
  'outputs': {'out': {'label': 'out',
    'type': 'string',
    'outputSource': 'iden-1-1/out'}},
  'steps': {'iden-1-1': {'run': 'iden',
    'in': {'arg': {'default': [4, 6, 8, 10]}},
    'out': ['out']}}}}

In [ ]:
from dewret.renderers.cwl import render
from dewret.tasks import construct, workflow, task
from dewret.annotations import AtRender

@task()
def work(arg: int) -> int:
    # do work
    return arg # need to return something or the loop is optimized away

@workflow()
def loop_work(list: AtRender[list[int]]) -> list[int]:
    result = []
    for i in list:
        res = work(arg = i)
        result.append(res) 

    return result

result = loop_work(list=[1,2])
workflow = construct(result, simplify_ids=True)
cwl = render(workflow)
cwl

{'__root__': {'cwlVersion': 1.2,
  'class': 'Workflow',
  'inputs': {},
  'outputs': {'out': {'label': 'out',
    'type': 'array',
    'items': 'int',
    'outputSource': 'loop_work-1/out'}},
  'steps': {'loop_work-1': {'run': 'loop_work',
    'in': {'list': {'default': [1, 2]}},
    'out': ['out']}}},
 'loop_work-1': {'cwlVersion': 1.2,
  'class': 'Workflow',
  'inputs': {},
  'outputs': [{'label': 'out', 'type': 'int', 'outputSource': 'work-1-1/out'},
   {'label': 'out', 'type': 'int', 'outputSource': 'work-1-2/out'}],
  'steps': {'work-1-1': {'run': 'work',
    'in': {'arg': {'default': 1}},
    'out': ['out']},
   'work-1-2': {'run': 'work',
    'in': {'arg': {'default': 2}},
    'out': ['out']}}}}

In [3]:
cwl['loop_work-1']['steps']

{'work-1-1': {'run': 'work', 'in': {'arg': {'default': 1}}, 'out': ['out']},
 'work-1-2': {'run': 'work', 'in': {'arg': {'default': 2}}, 'out': ['out']}}

## Not working, as designed


Error message is helpful


In [11]:
from dewret.renderers.cwl import render
from dewret.tasks import construct, workflow, task

list_2: list[int] = [0, 1, 2, 3]

@task()
def iden(arg: str) -> str:
    return arg

@workflow()
def loop_over_lists() -> list[int]:
    result = []
    for a, b in zip(list_2, list_2, strict=False):
        result.append(a + b + len(list_2))
    return iden(arg = result)

result = loop_over_lists()
workflow = construct(result, simplify_ids=True)
cwl = render(workflow)
cwl

TaskException: This iterable reference does not have a known fixed length, consider using `Fixed[...]` with a default, or typehint using `tuple[int, float]` (or similar) to tell dewret how long it should be.